In [1]:
import requests
from requests.exceptions import HTTPError
import pandas as pd
from fake_useragent import UserAgent
from dataclasses import dataclass
from typing import Any, Callable, Iterable, List, Mapping, MutableMapping, Optional, Tuple, Union

from urllib.parse import (
    urljoin,
    urlparse,
    parse_qs
    )

import duckdb

pd.set_option("display.max_columns", 100)


In [2]:
@dataclass
class Scraper:
    url_base: str = "http://albertare.com/api/"
    path: str = "properties"
    page_limit: str = "100"
    minprice: str = "200000"
    status: str = "s"
    max_days_listed: str = None
    city: str = None
    jwt_token: str = "eyJ0eXAiOiJKV1QiLCJhbGciOiJIUzI1NiJ9.eyJpc3MiOiJodHRwczovL2FsYmVydGFyZS5jb20vYXBpL2xlYWRzL3JlZ2lzdGVyL2NvbXBsZXRlIiwiaWF0IjoxNjU2NzkwMjY0LCJleHAiOjE2NTczOTUwNjQsIm5iZiI6MTY1Njc5MDI2NCwianRpIjoiM2s0RWFYN2J4R3FaSG83ciIsInN1YiI6MjIxNTc0MSwicHJ2IjoiMTVmNWM4MTQ1MThiZmY5ZjVmZmUzZGUzYzRhNWUzMzFkNGY2MmFlNCIsImVtYWlsIjoicGFydHlnaXJsc3Jvb20zMTRAZ21haWwuY29tIiwiZW1haWxTdGF0dXMiOiJ2YWxpZF9hZGRyZXNzIiwiZmlyc3ROYW1lIjoiUGFydHkiLCJsYXN0TmFtZSI6IkdpcmwiLCJwaG9uZSI6IisxMzA2MjIyMjM0NyIsInBob25lU3RhdHVzIjoidmFsaWRfbnVtYmVyIiwiYnV5ZXJBZ2VudElkIjozMjkzLCJsZW5kZXJJZCI6bnVsbCwiY29tcGxldGVkIjp0cnVlLCJoYXNDb0J1eWVyIjpmYWxzZSwicmVsYXRlZExlYWRGaXJzdE5hbWUiOm51bGx9.TetdaJRb_V1s2EU3aIIRHkTjl5JAXzkONpPIwOWVhS0"
    
    def __init__(self):
        self._session = requests.Session()
        
    @property
    def http_method(self) -> str:
        """
        Override if needed. See get_request_data/get_request_json if using POST/PUT/PATCH.
        """
        return "GET"
    
    @property
    def data_field(self):
        return "data"
    
    def _create_prepared_request(
        self,
        path: str,
        headers: Mapping = None,
        params: Mapping = None,
        json: Any = None,
        data: Any = None
    ) -> requests.PreparedRequest:
        args = {"method": self.http_method, "url": urljoin(self.url_base, path), "headers": headers, "params": params}
        if json and data:
            raise requests.RequestException(
                    "At the same time only one of the 'request_body_data' and 'request_body_json' functions can return data"
                )
        elif json:
                args["json"] = json
        elif data:
                args["data"] = data
                
        return self._session.prepare_request(requests.Request(**args))
        
    
    def get_user_agent(self):
            return UserAgent(verify_ssl=False).random
    
    def get_headers(self):
        headers = {
            "Accept": "application/json",
            "User-Agent": self.get_user_agent(),
            "Authorization": f"Bearer {self.jwt_token}"
        }
        return headers
    
    def request_params(self, next_page_token: Mapping[str, Any] = None):
        params = {
            
            #"city": city,
            "status": self.status,
            "minprice": self.minprice,
            "cf_ds": "created_at asc",
            "maxdayslisted": self.max_days_listed,
            "city": self.city,
            "limit": self.page_limit 
        }
        
        if next_page_token:
            params.update(next_page_token)
        
        return params
    
    def request_kwargs(
        self,
        next_page_token: Mapping[str, Any] = None,
    ) -> Mapping[str, Any]:
        """
        Override to return a mapping of keyword arguments to be used when creating the HTTP request.
        Any option listed in https://docs.python-requests.org/en/latest/api/#requests.adapters.BaseAdapter.send for can be returned from
        this method. Note that these options do not conflict with request-level options such as headers, request params, etc..
        """
        return {}
        
    def next_page_token(self, response: requests.Response):
        """
        Uses a cursor-based pagination strategy.
        Extract the cursor from the response if it exists and return it in a format
        that can be used to update request parameters
        :param response: the most recent response from the API
        :return If there is another page in the result, a mapping (e.g: dict) containing information needed to query the next page in the response.
                If there are no more pages in the result, return None.
        """
        
        json_response = response.json()
        links = json_response.get("meta",{}).get("pagination",{}).get("links",{})
        if "next" in links:
            next_page = links.get("next")
            print(f"Getting page: {next_page}")
        else:
            next_page = None
        
        if next_page:
            next = urlparse(next_page).query
            return {"page": parse_qs(next)["page"][0]}
        
        
        
    def parse_response(self, response: requests.Response, **kwargs) -> Iterable[Mapping]:
        json_response = response.json()
        yield from json_response.get(self.data_field, []) 
        
    
    def read_records(self)->Iterable[Mapping[str, Any]]:
        pagination_complete = False
        next_page_token = None
        
        while not pagination_complete:
            request_headers = self.get_headers()
            request = self._create_prepared_request(
                path = self.path,
                headers=request_headers,
                params=self.request_params(next_page_token=next_page_token)
            )
            
            request_kwargs = self.request_kwargs(next_page_token=next_page_token)
            
            response = self._session.send(request, **request_kwargs)
            try:
                yield from self.parse_response(response)
            
                next_page_token =  self.next_page_token(response)
                if not next_page_token:
                    pagination_complete = True
            except HTTPError as e:
                print(e)
                
        
        # Always return an empty generator just in case no records were ever yielded
        yield from []
        
        

In [3]:
scraper = Scraper()
#scraper.max_days_listed = "90"
#scraper.city = "Edmonton"

In [4]:
data = scraper.read_records()

In [9]:
d = []
for i in data:
    d.append(i)

Getting page: https://albertare.com/api/properties?status=s&minprice=200000&cf_ds=created_at%20asc&limit=100&page=2
Getting page: https://albertare.com/api/properties?status=s&minprice=200000&cf_ds=created_at%20asc&limit=100&page=3
Getting page: https://albertare.com/api/properties?status=s&minprice=200000&cf_ds=created_at%20asc&limit=100&page=4
Getting page: https://albertare.com/api/properties?status=s&minprice=200000&cf_ds=created_at%20asc&limit=100&page=5
Getting page: https://albertare.com/api/properties?status=s&minprice=200000&cf_ds=created_at%20asc&limit=100&page=6
Getting page: https://albertare.com/api/properties?status=s&minprice=200000&cf_ds=created_at%20asc&limit=100&page=7
Getting page: https://albertare.com/api/properties?status=s&minprice=200000&cf_ds=created_at%20asc&limit=100&page=8
Getting page: https://albertare.com/api/properties?status=s&minprice=200000&cf_ds=created_at%20asc&limit=100&page=9
Getting page: https://albertare.com/api/properties?status=s&minprice=200

KeyboardInterrupt: 

In [12]:
d[-1]

{'id': '53468363',
 'attributes': {'created_at': '2021-08-05T11:24:47-04:00',
  'updated_at': '2022-01-01T07:36:15-05:00',
  'listed_at': '2021-07-11T00:00:00-04:00',
  'mls': 'A1128762',
  'street': 'Mount Crandell Crescent West',
  'address': '200 Mount Crandell Crescent West',
  'city': 'Lethbridge',
  'state': 'AB',
  'zip': 'T1K 6M2',
  'neighborhood': 'Mountain Heights',
  'area': None,
  'county': 'Lethbridge',
  'price': 271500,
  'status': 'Sold',
  'type': 'Home',
  'description': 'Is the heat getting to you come take a look at this Unique BI/Level floor plan with central air. Home has been freshly painted. Very open floor plan. On the main floor you will find open concept Livingroom and kitchen room for the whole family, five bed two baths home. Large deck off kitchen also freshly painted. Great place for all those family BBQs. Lower level offers big windows for loads of natural light. Large family room for the kids or maybe that man cave you’ve always dreamed of. Also in lo

In [13]:
df = pd.json_normalize(d)

In [14]:
df.head()

id      attributes.created_at      attributes.updated_at  \
0  61482689  2022-07-01T21:30:40-04:00  2022-07-01T21:30:40-04:00   
1  61482495  2022-07-01T21:10:08-04:00  2022-07-01T21:10:08-04:00   
2  61482177  2022-07-01T20:49:20-04:00  2022-07-01T20:49:20-04:00   
3  61480347  2022-07-01T19:16:43-04:00  2022-07-03T20:08:11-04:00   
4  61470055  2022-07-01T14:36:59-04:00  2022-07-01T14:36:59-04:00   

        attributes.listed_at attributes.mls      attributes.street  \
0  2021-07-04T00:00:00-04:00       A1119089          Range Road 25   
1  2022-06-24T00:00:00-04:00       A1233452  Arbour Stone Close NW   
2  2022-06-16T00:00:00-04:00       A1229899          Range Road 30   
3  2022-06-15T00:00:00-04:00       A1229913        Bermuda Road NW   
4  2022-06-29T00:00:00-04:00       A1234460        FALMEAD Road NE   

          attributes.address        attributes.city attributes.state  \
0       431004 Range Road 25    Rural Ponoka County               AB   
1  152 Arbour Stone Close NW                Calgary               AB   
2  35468 Range Road 30 #1077  Rural Red Deer County               AB   
3         40 Bermuda Road NW                Calgary               AB   
4         44 FALMEAD Road NE                Calgary               AB   

  attributes.zip attributes.neighborhood attributes.area attributes.county  \
0        T4J 1R2                    None            None     Ponoka County   
1        T3G 4T2             Arbour Lake            None           Calgary   
2        T4G 0M3          Gleniffer Lake            None   Red Deer County   
3        T3K 1G6      Beddington Heights            None           Calgary   
4        T3J 1G8             Falconridge            None           Calgary   

   attributes.price attributes.status attributes.type  \
0         1150000.0              Sold            Home   
1          650000.0              Sold            Home   
2          390000.0              Sold            Home   
3          503000.0              Sold            Home   
4          330000.0              Sold            Home   

                              attributes.description  attributes.is_for_rent  \
0  Breathtaking property centrally located within...                   False   
1  Welcome to the exquisitely redesigned and prof...                   False   
2  PHASE 1 LOT 77 GLENIFFER LAKE GOLF AND COUNTRY...                   False   
3  PRICED for a QUICK SALE ! CHECKOUT this AMAZIN...                   False   
4  3 Bedrooms Single family detatched gungalow ha...                   False   

   attributes.is_for_sale  attributes.bedrooms  attributes.bathrooms  \
0                    True                  5.0                   4.0   
1                    True                  3.0                   4.0   
2                    True                  2.0                   2.0   
3                    True                  4.0                   3.0   
4                    True                  3.0                   1.0   

   attributes.half_bathrooms  attributes.square  attributes.lot_square  \
0                        1.0             4512.0               196455.6   
1                        1.0             1749.7                 4356.0   
2                        NaN              857.0                 2613.6   
3                        1.0             1562.0                 4791.6   
4                        NaN             1520.0                 4356.0   

  attributes.broker attributes.agent  attributes.year attributes.virtual_tour  \
0              None        Cahellobr           2001.0                    None   
1              None                            2001.0                    None   
2              None        Cawiznica           2016.0                    None   
3              None         Cgilleky           1979.0                    None   
4              None                            1980.0                    None   

   attributes.images_total  attributes.garages_total attributes.parking_total  \
0

In [64]:
dfs = []
error = []
for df in data:
    print(sys.exc_info())
    try:
        dfs.append(pd.json_normalize(df))
    except:
        error.append(df)
        

In [25]:
d = requests.get("https://albertare.com/api/properties?status=s&minprice=200000&cf_ds=created_at%20asc&limit=100&page=562")
d

<Response [200]>

In [35]:
len(dfs)

2200

In [396]:
pd.json_normalize(x["attributes"])

created_at                 updated_at  \
0  2022-06-27T11:41:02-04:00  2022-06-30T18:39:03-04:00   

                   listed_at       mls         street               address  \
0  2022-04-20T00:00:00-04:00  A1206739  Range Road 31  243142 Range Road 31   

                      city state      zip neighborhood  area  \
0  Rural Rocky View County    AB  T3Z 3L7   Springbank  None   

              county    price status  type  \
0  Rocky View County  2132500   Sold  Home   

                                         description  is_for_rent  \
0  A custom-built character walkout home in the c...        False   

   is_for_sale  bedrooms  bathrooms  half_bathrooms  square  lot_square  \
0         True         4          6               2  4001.5      267894   

  broker agent  year virtual_tour  images_total  garages_total parking_total  \
0   None        1981         None            48              4          None   

  style           price_reduced_at schools                   city_label  \
0  None  2022-06-30T18:39:03-04:00    None  Rural Rocky View County, AB   

      rating  isManuallyRated ratingInfo  is_active mls_neighborhood  \
0  Fair Deal            False       None       True       Springbank   

   tax_amount  hoa_dues  location.lon  location.lat  
0           0         0   -114.302522     51.060484

In [386]:
import numpy as np
np.array(list(x.items()))

array([['id', '61388441'],
       ['attributes',
        {'created_at': '2022-06-27T11:41:02-04:00', 'updated_at': '2022-06-30T18:39:03-04:00', 'listed_at': '2022-04-20T00:00:00-04:00', 'mls': 'A1206739', 'street': 'Range Road 31', 'address': '243142 Range Road 31', 'city': 'Rural Rocky View County', 'state': 'AB', 'zip': 'T3Z 3L7', 'neighborhood': 'Springbank', 'area': None, 'county': 'Rocky View County', 'price': 2132500, 'status': 'Sold', 'type': 'Home', 'description': "A custom-built character walkout home in the community of Springbank offering over 5800 sq. ft of developed living space and boasts pride of ownership throughout! The 6-acre parcel allows for livestock - you could have a horse, chickens, or other animals! This home features sprawling family and entertaining spaces including a large open concept kitchen, dining and family room with access to a huge West facing deck with amazing views. Experience extensive design details from hand crafted lighting, custom ironwork, woo

In [380]:
con = duckdb.connect(database="alberta-re-db.duckdb", read_only=False)

In [308]:
# scraper = Scraper()
# records = scraper.read_records()
# dfs = []
# exceptions = []
# for r in records:
#     try:
#         dfs.append(pd.json_normalize(r))
#         print("Getting data")
#     except:
#         exceptions.append(r)
#         print("Exception!")
        


In [38]:
url = urljoin(scraper.url_base, scraper.path)
headers = scraper.get_headers()
params = scraper.request_params()

In [66]:
import logging
logger = logging.Logger(name="AB-RE")
r = requests.get(url=url, headers=headers, params=params)
for i in range(1,10,1):
    
    params["page"] = i
    r = requests.get(url=url, headers=headers, params=params)
    print(r.status_code)
    


200
200
200
200


KeyboardInterrupt: 

In [67]:
r.content

b'{"data":[{"id":"61298327","attributes":{"created_at":"2022-06-22T13:01:45-04:00","updated_at":"2022-06-30T21:05:16-04:00","listed_at":"2022-05-07T00:00:00-04:00","mls":"A1211735","street":"Henner\'s Outlook","address":"11 Henner\'s Outlook","city":"Lacombe","state":"AB","zip":"T4L 1Z3","neighborhood":"Henner\'s Landing","area":null,"county":"Lacombe","price":735000,"status":"Sold","type":"Home","description":"Welcome to this custom built, ABSOLUTELY STUNNING two story home! You wont find another home like this in town. Greeted by UNIQUE DESIGNS and GRAND DETAILING, this home boasts a large front entrance, exquisite CUSTOM RAILINGS, open concept kitchen, and inviting main floor living room. Soaring 22 FT walls are complimented by a floor to ceiling stone gas fireplace, warming up the living space and creating an impressive focal point. The kitchen boasts an impressive amount of CUSTOM CABINETRY, GRANITE countertops, GAS COOKTOP, HOOD FAN, POT FILLER, ISLAND WITH EXTRA SEATING and WINE

In [61]:
requests.get(url=urljoin("https://albertare.com", "homedetails/61491853-402-2-avenue-oyen-ab-t0j-2j0"), headers=headers).json()

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [ ]:
 /homedetails/61491853-402-2-avenue-oyen-ab-t0j-2j0

In [48]:
r.json()

{'data': [{'id': '59952221',
   'attributes': {'created_at': '2022-04-20T05:53:16-04:00',
    'updated_at': '2022-05-01T04:56:09-04:00',
    'listed_at': '2022-03-30T00:00:00-04:00',
    'mls': 'A1199702',
    'street': 'Strathcona Drive SW',
    'address': '1617 Strathcona Drive SW',
    'city': 'Calgary',
    'state': 'AB',
    'zip': 'T3H 5B1',
    'neighborhood': 'Strathcona Park',
    'area': None,
    'county': 'Calgary',
    'price': 755000,
    'status': 'Sold',
    'type': 'Home',
    'description': 'LOCATION, LOCATION, LOCATION! In the sought-after neighborhood of Strathcona Park you’ll find this STUCCO and STONE, beautiful CURB APPEAL, 2-storey home with over 3300 SQFT OF LIVING SPACE. As you enter this home, you’re greeted by the spacious living room and formal dining room with HARDWOOD FLOORS. To the left of the main door is a ½ bath, den, and laundry room with a door to the double attached garage. The kitchen is well laid out and has GRANITE counters, PLENTY OF CABINETS, 

In [57]:
""" Models for validation pubsub payloads """
from typing import Optional
import base64
from pydantic import BaseModel, Field 
import json

class BaseModelWithPubSub(BaseModel):
    """ Extra decode functions for pubsub data """

    @classmethod
    def from_base64(cls, data: bytes):
        return cls.parse_raw(base64.b64decode(data).decode("utf-8"))

    @classmethod
    def from_event(cls, event: dict):
        return cls.from_base64(event["ride"])


class RideFeatures(BaseModelWithPubSub):
    """ Ride feature data """
    PULOCATIONID: str = Field(..., title="Pickup Location ID")
    DOLOCATIONID: str = Field(..., title="Dropoff Location ID")
    TRIP_DISTANCE: int = Field(..., title="Trip distance")
    
class RideData(BaseModelWithPubSub):
    """ Ride event data """
    ride: Optional[RideFeatures] = None
    ride_id: str

In [76]:
ride_event = {
    "ride":{
            "PULOCATIONID": "101",
            "DOLOCATIONID": "69",
            "TRIP_DISTANCE": 14.55
            },
    "ride_id": "1234"
}

In [84]:
def send(ride: RideData):
    result = json.dumps(ride).encode("utf-8")
    print(result)
    return result

In [85]:
event = send(ride_event)


b'{"ride": {"PULOCATIONID": "101", "DOLOCATIONID": "69", "TRIP_DISTANCE": 14.55}, "ride_id": "1234"}'


In [83]:
event.from_event()

AttributeError: 'dict' object has no attribute 'from_event'

In [60]:
ride = RideData.from_base64(ride_event)

TypeError: argument should be a bytes-like object or ASCII string, not 'dict'

In [35]:
class RideFeatures(BaseModel):
    """ Ride feature data """
    PULOCATIONID: str = Field(..., title="Pickup Location ID")
    DOLOCATIONID: str = Field(..., title="Dropoff Location ID")
    TRIP_DISTANCE: int = Field(..., title="Trip distance")
    
class RideData(BaseModel):
    """ Ride event data """
    ride: Optional[RideFeatures] = None
    ride_id: str

In [47]:
event = {
        "ride":
                {
                "PULOCATIONID": "101",
                "DOLOCATIONID": "69",
                "TRIP_DISTANCE": 14.55
                },
        "ride_id": "123"
        }

In [48]:
ride_data = RideData.parse_obj(ride_event)

In [50]:
ride_data.dict

<bound method BaseModel.dict of RideData(ride=RideFeatures(PULOCATIONID='101', DOLOCATIONID='69', TRIP_DISTANCE=14), ride_id='123')>

In [26]:
def send(ride: RideFeatures):
    ride_parsed = ride.from_event()
    return ride_parsed

In [27]:
ride = {
    "data":{
        "PULOCATIONID": "101",
        "DOLOCATIONID": "69",
        "TRIP_DISTANCE": 14.55
        }
}

In [28]:
send(ride=ride)

AttributeError: 'dict' object has no attribute 'from_event'